################################################################################
> # **Part - I**

*   define actor critic networks
*   define PPO algorithm

################################################################################

In [1]:


############################### Import libraries ###############################


import os
import glob
import time
from datetime import datetime

import torch
import torch.nn as nn
from torch.distributions import MultivariateNormal
from torch.distributions import Categorical

import numpy as np

import gym
import pongGym

################################## set device ##################################

print("============================================================================================")


# set device to cpu or cuda
device = torch.device('cpu')

# if(torch.cuda.is_available()): 
#     device = torch.device('cuda:0') 
#     torch.cuda.empty_cache()
#     print("Device set to : " + str(torch.cuda.get_device_name(device)))
# else:
#     print("Device set to : cpu")
    
# print("============================================================================================")




################################## PPO Policy ##################################


class RolloutBuffer:
    def __init__(self):
        self.actions = []
        self.states = []
        self.logprobs = []
        self.rewards = []
        self.is_terminals = []
    

    def clear(self):
        del self.actions[:]
        del self.states[:]
        del self.logprobs[:]
        del self.rewards[:]
        del self.is_terminals[:]


class ActorCritic(nn.Module):
    def __init__(self, state_dim, action_dim, action_std_init):
        super(ActorCritic, self).__init__()

        
        self.actor = nn.Sequential(
                        nn.Linear(state_dim, 64),
                        nn.ReLU(),
                        nn.Linear(64, 64),
                        nn.ReLU(),
                        nn.Linear(64, action_dim),
                        nn.Softmax(dim=-1)
                    )

        
        # critic
        self.critic = nn.Sequential(
                        nn.Linear(state_dim, 64),
                        nn.ReLU(),
                        nn.Linear(64, 64),
                        nn.ReLU(),
                        nn.Linear(64, 1)
                    )

    def forward(self):
        raise NotImplementedError
    

    def act(self, state):

        
        action_probs = self.actor(state)
        dist = Categorical(action_probs)

        action = dist.sample()
        action_logprob = dist.log_prob(action)
        
        return action.detach(), action_logprob.detach()
    

    def evaluate(self, state, action):


        action_probs = self.actor(state)
        dist = Categorical(action_probs)

        action_logprobs = dist.log_prob(action)
        dist_entropy = dist.entropy()
        state_values = self.critic(state)
        
        return action_logprobs, state_values, dist_entropy


class PPO:
    def __init__(self, state_dim, action_dim, lr_actor, lr_critic, gamma, K_epochs, eps_clip, action_std_init=0.6):

        self.gamma = gamma
        self.eps_clip = eps_clip
        self.K_epochs = K_epochs
        
        self.buffer = RolloutBuffer()

        self.policy = ActorCritic(state_dim, action_dim, action_std_init).to(device)
        self.optimizer = torch.optim.Adam([
                        {'params': self.policy.actor.parameters(), 'lr': lr_actor},
                        {'params': self.policy.critic.parameters(), 'lr': lr_critic}
                    ])

        self.policy_old = ActorCritic(state_dim, action_dim, action_std_init).to(device)
        self.policy_old.load_state_dict(self.policy.state_dict())
        
        self.MseLoss = nn.MSELoss()


    def select_action(self, state):

        with torch.no_grad():
            state = torch.FloatTensor(state).to(device)
            action, action_logprob = self.policy_old.act(state)

        self.buffer.states.append(state)
        self.buffer.actions.append(action)
        self.buffer.logprobs.append(action_logprob)

        return action.item()


    def update(self):

        # Monte Carlo estimate of returns
        rewards = []
        discounted_reward = 0
        for reward, is_terminal in zip(reversed(self.buffer.rewards), reversed(self.buffer.is_terminals)):
            if is_terminal:
                discounted_reward = 0
            discounted_reward = reward + (self.gamma * discounted_reward)
            rewards.insert(0, discounted_reward)
            
        # Normalizing the rewards
        rewards = torch.tensor(rewards, dtype=torch.float32).to(device)
        rewards = (rewards - rewards.mean()) / (rewards.std() + 1e-7)

        # convert list to tensor
        old_states = torch.squeeze(torch.stack(self.buffer.states, dim=0)).detach().to(device)
        old_actions = torch.squeeze(torch.stack(self.buffer.actions, dim=0)).detach().to(device)
        old_logprobs = torch.squeeze(torch.stack(self.buffer.logprobs, dim=0)).detach().to(device)

        
        # Optimize policy for K epochs
        for _ in range(self.K_epochs):

            # Evaluating old actions and values
            logprobs, state_values, dist_entropy = self.policy.evaluate(old_states, old_actions)

            # match state_values tensor dimensions with rewards tensor
            state_values = torch.squeeze(state_values)
            
            # Finding the ratio (pi_theta / pi_theta__old)
            ratios = torch.exp(logprobs - old_logprobs.detach())

            # Finding Surrogate Loss
            advantages = rewards - state_values.detach()   
            surr1 = ratios * advantages
            surr2 = torch.clamp(ratios, 1-self.eps_clip, 1+self.eps_clip) * advantages

            # final loss of clipped objective PPO
            loss = -torch.min(surr1, surr2) + 0.5*self.MseLoss(state_values, rewards) - 0.01*dist_entropy
            
            # take gradient step
            self.optimizer.zero_grad()
            loss.mean().backward()
            self.optimizer.step()
            
        # Copy new weights into old policy
        self.policy_old.load_state_dict(self.policy.state_dict())

        # clear buffer
        self.buffer.clear()
    
    
    def save(self, checkpoint_path):
        torch.save(self.policy_old.state_dict(), checkpoint_path)
   

    def load(self, checkpoint_path):
        self.policy_old.load_state_dict(torch.load(checkpoint_path, map_location=lambda storage, loc: storage))
        self.policy.load_state_dict(torch.load(checkpoint_path, map_location=lambda storage, loc: storage))
        
        
       



pygame 2.1.0 (SDL 2.0.16, Python 3.9.7)
Hello from the pygame community. https://www.pygame.org/contribute.html


################################################################################
> # **Part - II**

*   train PPO algorithm on environments
*   save preTrained networks weights and log files

################################################################################

In [4]:


max_ep_len = 400
print_freq = max_ep_len * 4     # print avg reward in the interval (in num timesteps)
log_freq = max_ep_len * 2       # log avg reward in the interval (in num timesteps)
save_model_freq = int(2e4)      # save model frequency (in num timesteps)

action_std = None

def TrainPong(config):
    env = pongGym.DoublePong()

    # state space dimension
    state_dim = env.observation_space.shape[0]

    # action space dimension

    action_dim = env.action_space.n


    # initialize a PPO agent
    ppo_agent = PPO(state_dim, action_dim, config["lr_actor"], config["lr_critic"], config["gamma"], config["K_epochs"],
                    config["eps_clip"], action_std)


    # track total training time
    start_time = datetime.now().replace(microsecond=0)


    # printing and logging variables
    print_running_reward = 0
    print_running_episodes = 0

    log_running_reward = 0
    log_running_episodes = 0

    time_step = 0
    i_episode = 0

    Max_reward = 0

    # training loop
    # env = pongGym.DoublePong()
    while i_episode <= 250:

        state = env.reset()
        current_ep_reward = 0
        for t in range(1, max_ep_len+1):

            # select action with policy
            action = ppo_agent.select_action(state)
            state, reward, done, _ = env.step(action)

            # saving reward and is_terminals
            ppo_agent.buffer.rewards.append(reward)
            ppo_agent.buffer.is_terminals.append(done)

            time_step +=1
            current_ep_reward += reward

            # update PPO agent
            if time_step % config["update_timestep"] == 0:
                ppo_agent.update()

            # printing average reward
            if time_step % print_freq == 0:

                # print average reward till last episode
                print_avg_reward = print_running_reward / print_running_episodes
                print_avg_reward = round(print_avg_reward, 2)

                print_running_reward = 0
                print_running_episodes = 0
            # break; if the episode is over
            if done:
                break

        print_running_reward += current_ep_reward
        print_running_episodes += 1

        log_running_reward += current_ep_reward
        log_running_episodes += 1

        i_episode += 1


    env.close()
    tune.report(avreward=print_avg_reward)





In [11]:
from ray import tune
from ray.tune.suggest import ConcurrencyLimiter
from ray.tune.suggest.bayesopt import BayesOptSearch

analysis = tune.run(
    TrainPong,
    config={
        "update_timestep":tune.randint(max_ep_len * 2, max_ep_len * 4),      # update policy every n timesteps
        "K_epochs": tune.randint(1, 60),               # update policy for K epochs
        "eps_clip": tune.uniform(0, 1),             # clip parameter for PPO
        "gamma": tune.uniform(0, 1),               # discount factor

        "lr_actor": tune.sample_from(lambda spec: np.random.uniform(0.000001, 0.1)),       # learning rate for actor network
        "lr_critic": tune.sample_from(lambda spec: np.random.uniform(0.000001, 0.1)),       # learning rate for critic network

        "random_seed": 0         # set random seed if required (0 = no random seed)
    },
#     search_alg=ConcurrencyLimiter(
#         BayesOptSearch(random_search_steps=4),
#         max_concurrent=2),
    stop={"avreward": 20},
    resources_per_trial={"cpu": 0.5},
    num_samples=400,
)

print("Best config: ", analysis.get_best_config(
    metric="avreward", mode="max"))

# Get a dataframe for analyzing trial results.
df = analysis.results_df

2021-12-15 13:07:44,393	WARNING tune.py:570 -- Tune detects GPUs, but no trials are using GPUs. To enable trials to use GPUs, set tune.run(resources_per_trial={'gpu': 1}...) which allows Tune to expose 1 GPU to each trial. You can also override `Trainable.default_resource_request` if using the Trainable API.


(bundle_reservation_check_func pid=143830) pygame 2.1.0 (SDL 2.0.16, Python 3.9.7)
(bundle_reservation_check_func pid=143830) Hello from the pygame community. https://www.pygame.org/contribute.html
(bundle_reservation_check_func pid=143829) pygame 2.1.0 (SDL 2.0.16, Python 3.9.7)
(bundle_reservation_check_func pid=143829) Hello from the pygame community. https://www.pygame.org/contribute.html
(bundle_reservation_check_func pid=143838) pygame 2.1.0 (SDL 2.0.16, Python 3.9.7)
(bundle_reservation_check_func pid=143838) Hello from the pygame community. https://www.pygame.org/contribute.html
(bundle_reservation_check_func pid=143827) pygame 2.1.0 (SDL 2.0.16, Python 3.9.7)
(bundle_reservation_check_func pid=143827) Hello from the pygame community. https://www.pygame.org/contribute.html
(bundle_reservation_check_func pid=143831) pygame 2.1.0 (SDL 2.0.16, Python 3.9.7)
(bundle_reservation_check_func pid=143831) Hello from the pygame community. https://www.pygame.org/contribute.html
(bundle_re

Result for TrainPong_efdbf_00021:
  avreward: -43.1
  date: 2021-12-15_13-09-26
  done: false
  experiment_id: 76558c125cee497da4926770c48e2f7b
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 144378
  time_since_restore: 96.07658672332764
  time_this_iter_s: 96.07658672332764
  time_total_s: 96.07658672332764
  timestamp: 1639544966
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: efdbf_00021
  
Result for TrainPong_efdbf_00021:
  avreward: -43.1
  date: 2021-12-15_13-09-26
  done: true
  experiment_id: 76558c125cee497da4926770c48e2f7b
  experiment_tag: 21_K_epochs=3,eps_clip=0.63985,gamma=0.48147,lr_actor=0.055802,lr_critic=0.09015,update_timestep=1019
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 144378
  time_since_restore: 96.07658672332764
  time_this_iter_s: 96.07658672332764
  time_total_s: 96.07658672332764
  timestamp: 1639544966
  timesteps_since_restore

Result for TrainPong_efdbf_00030:
  avreward: -75.52
  date: 2021-12-15_13-09-33
  done: false
  experiment_id: f910ed832a8742d4a0f4a4a9fe1af934
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 144404
  time_since_restore: 102.62529420852661
  time_this_iter_s: 102.62529420852661
  time_total_s: 102.62529420852661
  timestamp: 1639544973
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: efdbf_00030
  
Result for TrainPong_efdbf_00030:
  avreward: -75.52
  date: 2021-12-15_13-09-33
  done: true
  experiment_id: f910ed832a8742d4a0f4a4a9fe1af934
  experiment_tag: 30_K_epochs=3,eps_clip=0.6612,gamma=0.77333,lr_actor=0.057006,lr_critic=0.053788,update_timestep=851
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 144404
  time_since_restore: 102.62529420852661
  time_this_iter_s: 102.62529420852661
  time_total_s: 102.62529420852661
  timestamp: 1639544973
  timesteps_since_

Result for TrainPong_efdbf_00008:
  avreward: -80.34
  date: 2021-12-15_13-09-43
  done: false
  experiment_id: 889e89c95b334da7a4678c37d4cb8f20
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 143842
  time_since_restore: 114.87813210487366
  time_this_iter_s: 114.87813210487366
  time_total_s: 114.87813210487366
  timestamp: 1639544983
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: efdbf_00008
  


...

Result for TrainPong_efdbf_00388:
  avreward: -25.3
  date: 2021-12-15_13-31-58
  done: false
  experiment_id: f51fa9daf12542c0986c78b456851185
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 166422
  time_since_restore: 108.15166306495667
  time_this_iter_s: 108.15166306495667
  time_total_s: 108.15166306495667
  timestamp: 1639546318
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: efdbf_00388
  
Result for TrainPong_efdbf_00388:
  avreward: -25.3
  date: 2021-12-15_13-31-58
  done: true
  experiment_id: f51fa9daf12542c0986c78b456851185
  experiment_tag: 388_K_epochs=46,eps_clip=0.16686,gamma=0.90386,lr_actor=0.094428,lr_critic=0.064295,update_timestep=949
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 166422
  time_since_restore: 108.15166306495667
  time_this_iter_s: 108.15166306495667
  time_total_s: 108.15166306495667
  timestamp: 1639546318
  timesteps_since

Result for TrainPong_efdbf_00392:
  avreward: -37.0
  date: 2021-12-15_13-31-59
  done: true
  experiment_id: 8fcf30c9ecea42c4a5de5a87d19ad78f
  experiment_tag: 392_K_epochs=49,eps_clip=0.41654,gamma=0.041173,lr_actor=0.083815,lr_critic=0.075761,update_timestep=1124
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 166611
  time_since_restore: 103.07325029373169
  time_this_iter_s: 103.07325029373169
  time_total_s: 103.07325029373169
  timestamp: 1639546319
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: efdbf_00392
  
Result for TrainPong_efdbf_00399:
  avreward: -52.0
  date: 2021-12-15_13-32-00
  done: false
  experiment_id: 713e345ba175412c89dee2b13bd87a18
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 167196
  time_since_restore: 53.96467185020447
  time_this_iter_s: 53.96467185020447
  time_total_s: 53.96467185020447
  timestamp: 1639546320
  timesteps_since_

Result for TrainPong_efdbf_00397:
  avreward: -32.2
  date: 2021-12-15_13-32-05
  done: false
  experiment_id: 9537c6f8a3954795a8ac88f25c1ef930
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 167078
  time_since_restore: 69.14274501800537
  time_this_iter_s: 69.14274501800537
  time_total_s: 69.14274501800537
  timestamp: 1639546325
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: efdbf_00397
  
Result for TrainPong_efdbf_00397:
  avreward: -32.2
  date: 2021-12-15_13-32-05
  done: true
  experiment_id: 9537c6f8a3954795a8ac88f25c1ef930
  experiment_tag: 397_K_epochs=58,eps_clip=0.2576,gamma=0.81208,lr_actor=0.045751,lr_critic=0.0080822,update_timestep=849
  hostname: grorge-System-Product-Name
  iterations_since_restore: 1
  node_ip: 10.123.52.233
  pid: 167078
  time_since_restore: 69.14274501800537
  time_this_iter_s: 69.14274501800537
  time_total_s: 69.14274501800537
  timestamp: 1639546325
  timesteps_since_resto

2021-12-15 13:32:06,905	INFO tune.py:626 -- Total run time: 1462.52 seconds (1462.36 seconds for the tuning loop).


Best config:  {'update_timestep': 912, 'K_epochs': 25, 'eps_clip': 0.11055668471343849, 'gamma': 0.39704937816765384, 'lr_actor': 0.04064081848566745, 'lr_critic': 0.009154599189606942, 'random_seed': 0}


In [12]:
print("Best config: ", analysis.get_best_config(
    metric="avreward", mode="max"))

# Get a dataframe for analyzing trial results.
df = analysis.results_df

Best config:  {'update_timestep': 912, 'K_epochs': 25, 'eps_clip': 0.11055668471343849, 'gamma': 0.39704937816765384, 'lr_actor': 0.04064081848566745, 'lr_critic': 0.009154599189606942, 'random_seed': 0}
